In [1]:
import altair as alt
import pandas as pd
import json
import folium
from folium import Choropleth
import geopandas as gpd
import numpy as np
import branca.colormap as cm
dati_reg = pd.read_csv('https://raw.githubusercontent.com/pcm-dpc/COVID-19/master/dati-regioni/dpc-covid19-ita-regioni.csv')


In [2]:
date=dati_reg.data.unique()
dati_reg_cln=dati_reg.loc[(dati_reg.denominazione_regione!='In fase di definizione/aggiornamento')]
dati_reg_cln.sort_values('denominazione_regione',axis=0,inplace=True)
dati_reg_cln.loc[(dati_reg.denominazione_regione=='Sardegna')]

data stato  codice_regione denominazione_regione  \
119   2020-02-29T17:00:00   ITA              20              Sardegna   
476   2020-03-17T17:00:00   ITA              20              Sardegna   
434   2020-03-15T17:00:00   ITA              20              Sardegna   
875   2020-04-05T17:00:00   ITA              20              Sardegna   
455   2020-03-16T17:00:00   ITA              20              Sardegna   
812   2020-04-02T17:00:00   ITA              20              Sardegna   
329   2020-03-10T18:00:00   ITA              20              Sardegna   
182   2020-03-03T18:00:00   ITA              20              Sardegna   
98    2020-02-28T18:00:00   ITA              20              Sardegna   
413   2020-03-14T17:00:00   ITA              20              Sardegna   
833   2020-04-03T17:00:00   ITA              20              Sardegna   
350   2020-03-11T17:00:00   ITA              20              Sardegna   
980   2020-04-10T17:00:00   ITA              20              Sardegna   
1085  2020-04-15T17:00:00   ITA              20              Sardegna   
392   2020-03-13T17:00:00   ITA              20              Sardegna   
854   2020-04-04T17:00:00   ITA              20              Sardegna   
1001  2020-04-11T17:00:00   ITA              20              Sardegna   
77    2020-02-27T18:00:00   ITA              20              Sardegna   
371   2020-03-12T17:00:00   ITA              20              Sardegna   
917   2020-04-07T17:00:00   ITA              20              Sardegna   
1022  2020-04-12T17:00:00   ITA              20              Sardegna   
1064  2020-04-14T17:00:00   ITA              20              Sardegna   
749   2020-03-30T17:00:00   ITA              20              Sardegna   
581   2020-03-22T17:00:00   ITA              20              Sardegna   
308   2020-03-09T18:00:00   ITA              20              Sardegna   
938   2020-04-08T17:00:00   ITA              20              Sardegna   
14    2020-02-24T18:00:00   ITA              20              Sardegna   
959   2020-04-09T17:00:00   ITA              20              Sardegna   
602   2020-03-23T17:00:00   ITA              20              Sardegna   
35    2020-02-25T18:00:00   ITA              20              Sardegna   
203   2020-03-04T17:00:00   ITA              20              Sardegna   
224   2020-03-05T17:00:00   ITA              20              Sardegna   
728   2020-03-29T17:00:00   ITA              20              Sardegna   
623   2020-03-24T17:00:00   ITA              20              Sardegna   
644   2020-03-25T17:00:00   ITA              20              Sardegna   
707   2020-03-28T17:00:00   ITA              20              Sardegna   
245   2020-03-06T17:00:00   ITA              20              Sardegna   
161   2020-03-02T18:00:00   ITA              20              Sardegna   
560   2020-03-21T17:00:00   ITA              20              Sardegna   
266   2020-03-07T18:00:00   ITA              20              Sardegna   
665   2020-03-26T17:00:00   ITA              20              Sardegna   
539   2020-03-20T17:00:00   ITA              20              Sardegna   
770   2020-03-31T17:00:00   ITA              20              Sardegna   
140   2020-03-01T17:00:00   ITA              20              Sardegna   
56    2020-02-26T18:00:00   ITA              20              Sardegna   
1043  2020-04-13T17:00:00   ITA              20              Sardegna   
896   2020-04-06T17:00:00   ITA              20              Sardegna   
791   2020-04-01T17:00:00   ITA              20              Sardegna   
518   2020-03-19T17:00:00   ITA              20              Sardegna   
287   2020-03-08T18:00:00   ITA              20              Sardegna   
686   2020-03-27T17:00:00   ITA              20              Sardegna   
497   2020-03-18T17:00:00   ITA              20              Sardegna   

            lat      long  ricoverati_con_sintomi  terapia_intensiva  \
119   39.215312  9.110616                       0                  0   
476   3

In [3]:
date=dati_reg_cln.data.unique()
dati_reg_cln_plt=dati_reg.loc[(dati_reg.data==date[-1])&(dati_reg.denominazione_regione!='In fase di definizione/aggiornamento')]
dati_reg_cln_plt.sort_values('denominazione_regione',axis=0,inplace=True)

C:\Users\simone\Anaconda3\lib\site-packages\ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  This is separate from the ipykernel package so we can avoid doing imports until


In [4]:
def plotting(regione):
    df_plotting=dati_reg_cln.melt(id_vars=['data','denominazione_regione'], value_vars=['totale_ospedalizzati', 'terapia_intensiva', 'ricoverati_con_sintomi','dimessi_guariti'],var_name='ospedalizzati e guariti',value_name='numero di persone')    
    df_plotting=df_plotting.loc[(df_plotting.denominazione_regione==regione)]
    df_plotting.sort_values('data',axis=0,inplace=True)
    source = df_plotting
    chart = alt.Chart(df_plotting).mark_line().encode(
        x='data:T',
        y='numero di persone:Q',
        color='ospedalizzati e guariti:N'
    )
    return chart.to_json()

In [5]:
lista_regioni = dati_reg_cln.denominazione_regione.unique()
lista_regioni

array(['Abruzzo', 'Basilicata', 'Calabria', 'Campania', 'Emilia-Romagna',
       'Friuli Venezia Giulia', 'Lazio', 'Liguria', 'Lombardia', 'Marche',
       'Molise', 'P.A. Bolzano', 'P.A. Trento', 'Piemonte', 'Puglia',
       'Sardegna', 'Sicilia', 'Toscana', 'Umbria', "Valle d'Aosta",
       'Veneto'], dtype=object)

In [6]:
diz={regione: plotting(regione) for regione in lista_regioni}

In [7]:
regioni = gpd.read_file("https://raw.githubusercontent.com/openpolis/geojson-italy/master/geojson/limits_IT_regions.geojson")
regioni_plt = regioni[["reg_name", "geometry"]].set_index("reg_name")
regioni_plt.sort_values('reg_name',inplace=True)

In [8]:
dati_reg_dict=dati_reg_cln_plt.groupby(['denominazione_regione'])['deceduti'].apply(lambda x: int(x.values))
dati_reg_dict['Trentino-Alto Adige/Südtirol']=dati_reg_dict['P.A. Bolzano']+dati_reg_dict['P.A. Trento']
dati_reg_dict.drop(['P.A. Bolzano','P.A. Trento'],inplace=True)
dati_reg_dict.sort_index(inplace=True)
dati_reg_dict.rename({'P.A. Trento':'Trentino-Alto Adige/Südtirol',
                      'Valle d\'Aosta':'Valle d\'Aosta/Vallée d\'Aoste',
                      'Emilia Romagna': 'Emilia-Romagna',
                          'Friuli Venezia Giulia': 'Friuli-Venezia Giulia'},inplace=True)

In [9]:
dati_reg_dict

denominazione_regione
Abruzzo                           76
Basilicata                         3
Calabria                          21
Campania                         109
Emilia-Romagna                  1344
Friuli-Venezia Giulia             87
Lazio                            124
Liguria                          358
Lombardia                       5944
Marche                           364
Molise                             9
Piemonte                         617
Puglia                            71
Sardegna                          26
Sicilia                           57
Toscana                          198
Trentino-Alto Adige/Südtirol     184
Umbria                            28
Valle d'Aosta/Vallée d'Aoste      41
Veneto                           362
Name: deceduti, dtype: int64

In [10]:
linear = cm.linear.Paired_08.scale(dati_reg_cln.deceduti.min(), dati_reg_cln.deceduti.max())#.to_step(n=15)
linear.caption = 'Numero di deceduti per regione'
linear

In [11]:
m = folium.Map(location=[42.351032,14.167546], tiles='cartodbpositron', zoom_start=5)

folium.GeoJson(
    regioni_plt,
    style_function=lambda feature: {
    'fillColor': linear(dati_reg_dict[feature['id']]),
    'opacity':1,
    'fill_opacity':0.9,
    'color' : 'black',
    'weight' : 0.3,
    'dashArray' : 0,
        }
    ).add_to(m)

for k,v in diz.items():
    popup_t = 'In {} sono decedute {} persone'.format(str(dati_reg_cln_plt.loc[(dati_reg_cln_plt.denominazione_regione==k),
                                                    ['denominazione_regione']].iloc[0]['denominazione_regione']), 
                                                    str(dati_reg_cln_plt.loc[(dati_reg_cln_plt.denominazione_regione==k),
                                                    ['deceduti']].iloc[0]['deceduti']))
                                                      
    folium.Marker(location=dati_reg_cln.loc[(dati_reg_cln.denominazione_regione==k),['lat','long']].iloc[0].to_list(),
                  tooltip=popup_t,
                  popup=folium.Popup(max_width=450).add_child(folium.VegaLite(v, width=450, height=250))).add_to(m)


m.add_child(linear)
m

In [12]:
m.save('regioni_interattiva_ext.html')